In [3]:
import numpy as np
import subprocess
import os
import shutil
import imageio
from calibrate import im_to_dat_with_gamma
from multiprocessing import Pool
# Where images are
im_dir = "/media/felix/Drive/Images/img_1"
# Where files will be written
use_path = "/home/felix/rapid_storage_1/Microscope/hugin"


In [4]:
# First we create the proper file structure, we make acopy as this is just helper to the actual julia scripts
# record data size (GB) vs time taken (s)
time_taken = {75:0}
file_dict = {}
for i in os.listdir(im_dir): # 39000_60814_40569_NoIR.dng
    x,y,z, descriptor = i.split("_")
    descriptor = descriptor.split(".")
    # For all hdr exp the exposure is written as time.0mus.dng cause float
    if len(descriptor) == 2:
        descriptor = descriptor[0]
    else:
        descriptor = '.'.join(descriptor[0:2])
    if descriptor not in file_dict.keys():
        file_dict[descriptor] = {}
    if z not in file_dict[descriptor].keys():
        file_dict[descriptor][z] = {}
    if y  not in file_dict[descriptor][z].keys():
        file_dict[descriptor][z][y] = []
    file_dict[descriptor][z][y].append(x)

In [7]:
# Make cleaned structure
# record data size (GB) vs time taken (s) (single thread)
time_taken = {75:32*60+7}
# Equiv single thread
time_taken_equiv = {}

pool = Pool(processes = 20)

def load_and_save(im_dir, x,y,z,descriptor):
    try: # We try applying gamma curve here to see how it affects results
        #print('retrieving data')
        dat = im_to_dat_with_gamma(im_dir+'/{}_{}_{}_{}.dng'.format(x,y,z,descriptor))
        #print('saving data')
        imageio.imsave(os.path.join(use_path,descriptor, z, y ,x+'.tiff'), dat)
        #print('saved data')
    except Exception as e:
        print('{} {} {} {} failed with error'.format(x,y,z,descriptor))
        print(e)
    return

# Keep track of processes 
results = []

if not os.path.isdir(use_path):
    os.mkdir(use_path)
for descriptor in file_dict.keys():
    os.mkdir(os.path.join(use_path,descriptor))
    for z in file_dict[descriptor].keys():
        os.mkdir(os.path.join(use_path,descriptor, z))
        for y in file_dict[descriptor][z].keys():
            os.mkdir(os.path.join(use_path,descriptor, z, y))
            for x in file_dict[descriptor][z][y]:
                res = pool.apply_async(load_and_save, (im_dir, x,y,z,descriptor))
                results.append(res)
                #load_and_save(im_dir, x,y,z,descriptor)


In [8]:
# HDR - if more than 1 descriptor
# record data size (GB) vs time taken (s)
time_taken = {297:50*60+28}
# Equiv single thread
time_taken_equiv = {}

def make_HDR(use_path,z,y,x): # Turns out this is by default threaded -- how to pass to gpu tho?
    # Create output file path
    out_fpath = os.path.join(use_path, 'HDR', z, y, x+ '.tiff') 
    # Wildcard to target all directories except HDR as the file wont exist yet
    use_files = os.path.join(use_path, '*', z, y, x+ '.tiff')
    cmd = 'enfuse -o {} {}'.format(out_fpath,use_files)
    os.system(cmd)
    return 

results = []

if len(file_dict.keys()) > 1:
    HDR = True
    if not os.path.isdir(os.path.join(use_path, 'HDR')):
        os.mkdir(os.path.join(use_path, 'HDR'))
    # We iterate the entire structure and put the result in the HDR stack - we dont care about exp iter so we use subdict
    sub_keys = file_dict[list(file_dict.keys())[0]]
    for z in sub_keys.keys():
        os.mkdir(os.path.join(use_path, 'HDR', z))
        for y in sub_keys[z].keys():
            os.mkdir(os.path.join(use_path, 'HDR', z, y))
            for x in sub_keys[z][y]:
                #pool.apply_async(make_HDR, (use_path,z,y,x))
                #results.append(res)
                make_HDR(use_path,z,y,x)
else:
    HDR = False

enfuse: /home/felix/miniconda3/lib/python3.10/site-packages/cv2/../../../../lib/libcurl.so.4: no version information available (required by /lib/x86_64-linux-gnu/libhdf5_serial.so.103)
enfuse: info: input image "/home/felix/rapid_storage_1/Microscope/hugin/exp32768.0mus/0/0/0.tiff" does not have an alpha channel;
enfuse: note: assuming all pixels should contribute to the final image
enfuse: info: input image "/home/felix/rapid_storage_1/Microscope/hugin/exp49152.0mus/0/0/0.tiff" does not have an alpha channel;
enfuse: note: assuming all pixels should contribute to the final image
enfuse: info: input image "/home/felix/rapid_storage_1/Microscope/hugin/exp65536mus/0/0/0.tiff" does not have an alpha channel;
enfuse: note: assuming all pixels should contribute to the final image
enfuse: info: input image "/home/felix/rapid_storage_1/Microscope/hugin/exp81920.0mus/0/0/0.tiff" does not have an alpha channel;
enfuse: note: assuming all pixels should contribute to the final image
enfuse: info:

In [9]:
# record data size (only hdr folder here) (GB) vs time taken (s)
time_taken = {65:0}
gray_projection = 'l-star'
contrast_window_size = 10
contrast_edge_scale = -0.3
save_path = "/home/felix/rapid_storage_1/Microscope/hugin_focused"
mask_dir = "/home/felix/rapid_storage_1/Microscope/masks"
if not os.path.isdir(save_path):
    os.mkdir(save_path)
if not os.path.isdir(mask_dir):
    os.mkdir(mask_dir)
# Change to this directory as masks are written to current directory
os.chdir(mask_dir)
# Again we only care about the subset
sub_keys = file_dict[list(file_dict.keys())[0]]
for z in sub_keys.keys():
    for y in sub_keys[z].keys():
        out_path = '{}/{}_{}.tiff'.format(save_path,z, y)
        # Generate path
        if HDR:
            in_path = os.path.join(use_path, 'HDR', z, y)+'/*'
        else:
            in_path = os.path.join(use_path, file_dict.keys()[0], z, y)+'/*'
        # Generate command
        cmd = 'enfuse -o {} --save-masks=%f_soft%E:%f_mask%E --exposure-weight=0 --saturation-weight=0 --contrast-weight=1 --hard-mask --gray-projector={} --contrast-window-size={} --contrast-edge-scale={} {}'.format(out_path,gray_projection,contrast_window_size,contrast_edge_scale, in_path)
        os.system(cmd)

enfuse: /home/felix/miniconda3/lib/python3.10/site-packages/cv2/../../../../lib/libcurl.so.4: no version information available (required by /lib/x86_64-linux-gnu/libhdf5_serial.so.103)
enfuse: warning: contrast window size "10" is even; increasing size to next odd number
enfuse: info: loading next image: /home/felix/rapid_storage_1/Microscope/hugin/HDR/0/0/0.tiff 1/1
TIFFWriteDirectorySec: Warning, Creating TIFF with legacy Deflate codec identifier, COMPRESSION_ADOBE_DEFLATE is more widely supported.
enfuse: info: loading next image: /home/felix/rapid_storage_1/Microscope/hugin/HDR/0/0/10500.tiff 1/1
TIFFWriteDirectorySec: Warning, Creating TIFF with legacy Deflate codec identifier, COMPRESSION_ADOBE_DEFLATE is more widely supported.
enfuse: info: loading next image: /home/felix/rapid_storage_1/Microscope/hugin/HDR/0/0/12000.tiff 1/1
TIFFWriteDirectorySec: Warning, Creating TIFF with legacy Deflate codec identifier, COMPRESSION_ADOBE_DEFLATE is more widely supported.
enfuse: info: load